In [170]:
import re
from numpy import array, argmax, random, take
import pandas as pd
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Embedding, RepeatVector
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import load_model
from tensorflow.keras import optimizers
import matplotlib.pyplot as plt
%matplotlib inline
import io
import json
import numpy as np

import random
import re
import tensorflow as tf
import unicodedata


from tensorflow.keras import layers
from tensorflow.keras.preprocessing.sequence import pad_sequences
pd.set_option('display.max_colwidth', 200)

In [152]:
import tensorflow as tf

In [87]:
filename="C:\\Users\\pc\\Downloads\\deu-eng\\deu.txt"
with open (filename,"r",encoding='utf-8') as file:
    line=file.read()
#line 

In [88]:
class clean_Text:
    def __init__(self,text):
        self.text=text
    def clean_text1(self):
        '''this is a 1st-method for cleaning the text'''
        text=self.text.strip().split("\n")
        text=[i.split("\t") for i in text]
        return text

In [89]:
obj_trans=clean_Text(line)

In [90]:
en_ger=obj_trans.clean_text1()

In [54]:
for l in range(len(en_ger)):
    print(en_ger[l].pop())

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [91]:
en_ger=[line[:-1] for line in en_ger]

In [106]:
en_ger[0:5]

[['Go.', 'Geh.'],
 ['Hi.', 'Hallo!'],
 ['Hi.', 'Grüß Gott!'],
 ['Run!', 'Lauf!'],
 ['Run.', 'Lauf!']]

In [136]:

import pandas as pd

#  list of lists
data =en_ger

# Convert the list of lists to a Pandas DataFrame
df = pd.DataFrame(data,columns=["English","German"])

df.head()

English      German
0     Go.        Geh.
1     Hi.      Hallo!
2     Hi.  Grüß Gott!
3    Run!       Lauf!
4    Run.       Lauf!

'Hi.'

In [124]:
en_ger[0:5]

[['Go.', 'Geh.'],
 ['Hi.', 'Hallo!'],
 ['Hi.', 'Grüß Gott!'],
 ['Run!', 'Lauf!'],
 ['Run.', 'Lauf!']]

In [129]:
english_words = [item[0] for item in en_ger]

In [131]:
german_words=[item[1] for item in en_ger]

In [138]:
#df["English"].to_listst()

In [142]:
# Unicode normalization
import unicodedata
def normalize_unicode(s):
    return ''.join(c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn')

In [143]:
def preprocess_sentence(s):
  s = normalize_unicode(s)
  s = re.sub(r"([?.!,¿])", r" \1 ", s)
  s = re.sub(r'[" "]+', " ", s)
  s = s.strip()
  return s

In [144]:
# Preprocess both the source and target sentences.
train_preprocessed_input = [preprocess_sentence(s) for s in english_words]
train_preprocessed_target = [preprocess_sentence(s) for s in german_words]

In [148]:
def tag_target_sentences(sentences):
  tagged_sentences = map(lambda s: (' ').join(['<sos>', s, '<eos>']), sentences)
  return list(tagged_sentences)

In [149]:
train_tagged_preprocessed_target = tag_target_sentences(train_preprocessed_target)

In [150]:
train_tagged_preprocessed_target[0]

'<sos> Geh . <eos>'

In [153]:
# Tokenizer for the Hungarian input sentences. Note how we're not filtering punctuation.
source_tokenizer = tf.keras.preprocessing.text.Tokenizer(oov_token='<unk>', filters='"#$%&()*+-/:;=@[\\]^_`{|}~\t\n')
source_tokenizer.fit_on_texts(train_preprocessed_input)
source_tokenizer.get_config()

{'num_words': None,
 'filters': '"#$%&()*+-/:;=@[\\]^_`{|}~\t\n',
 'lower': True,
 'split': ' ',
 'char_level': False,
 'oov_token': '<unk>',
 'document_count': 261499,
 'word_counts': '{"go": 5439, ".": 219871, "hi": 42, "run": 399, "!": 1356, "wow": 15, "duck": 4, "fire": 411, "help": 3178, "stay": 1307, "stop": 1184, "wait": 978, "begin": 148, "do": 18079, "it": 16411, "on": 8694, "hello": 73, "hurry": 334, "i": 54971, "hid": 112, "ran": 446, "see": 2974, "try": 930, "won": 209, "oh": 49, "no": 3860, "relax": 53, "shoot": 71, "smile": 155, "sorry": 675, "?": 43471, "ask": 1232, "me": 14272, "attack": 68, "buy": 1192, "cheers": 2, "eat": 1610, "up": 4303, "freeze": 12, "now": 3232, "got": 2984, "he": 16684, "hop": 2, "in": 18194, "hug": 57, "care": 629, "fell": 486, "fled": 12, "know": 8112, "lied": 163, "lost": 962, "paid": 329, "pass": 230, "sang": 80, "spit": 9, "swim": 479, "wept": 7, "i\'m": 9230, "19": 13, "ok": 343, "listen": 372, "way": 1631, "really": 3521, "thanks": 283, "w

In [154]:
source_vocab_size = len(source_tokenizer.word_index) + 1
print(source_vocab_size)

17433


In [155]:
# Tokenizer for the german target sentences.
target_tokenizer = tf.keras.preprocessing.text.Tokenizer(oov_token='<unk>', filters='"#$%&()*+-/:;=@[\\]^_`{|}~\t\n')
target_tokenizer.fit_on_texts(train_tagged_preprocessed_target)
target_tokenizer.get_config()

{'num_words': None,
 'filters': '"#$%&()*+-/:;=@[\\]^_`{|}~\t\n',
 'lower': True,
 'split': ' ',
 'char_level': False,
 'oov_token': '<unk>',
 'document_count': 261499,
 'word_counts': '{"<sos>": 261499, "geh": 294, ".": 210011, "<eos>": 261499, "hallo": 71, "!": 11545, "gru\\u00df": 23, "gott": 93, "lauf": 19, "potzdonner": 3, "donnerwetter": 3, "kopf": 256, "runter": 67, "feuer": 231, "hilfe": 991, "zu": 24541, "hulf": 1, "bleib": 112, "stopp": 2, "anhalten": 29, "warte": 272, "fang": 28, "an": 7373, "mache": 467, "es": 22831, "tue": 230, "mach": 463, "weiter": 408, "sers": 1, "beeil": 44, "dich": 5793, "schnell": 846, "ich": 69933, "versteckte": 73, "mich": 9305, "habe": 12374, "versteckt": 109, "rannte": 157, "verstehe": 386, "aha": 2, "versuche": 179, "probiere": 17, "hab": 153, "gewonnen": 196, "oh": 17, ",": 72430, "nein": 142, "entspann": 17, "schie\\u00df": 4, "lacheln": 153, "entschuldigung": 122, "?": 43430, "frag": 107, "fragt": 59, "fragen": 938, "sie": 27650, "angriff": 2

In [156]:
target_vocab_size = len(target_tokenizer.word_index) + 1
print(target_vocab_size)

38113


In [157]:
train_encoder_inputs = source_tokenizer.texts_to_sequences(train_preprocessed_input)

In [158]:
print(train_encoder_inputs[:3])
print(source_tokenizer.sequences_to_texts(train_encoder_inputs[:3]))

[[49, 2], [2240, 2], [2240, 2]]
['go .', 'hi .', 'hi .']


In [159]:
def generate_decoder_inputs_targets(sentences, tokenizer):
  seqs = tokenizer.texts_to_sequences(sentences)
  decoder_inputs = [s[:-1] for s in seqs] # Drop the last token in the sentence.
  decoder_targets = [s[1:] for s in seqs] # Drop the first token in the sentence.

  return decoder_inputs, decoder_targets

In [160]:
train_decoder_inputs, train_decoder_targets = generate_decoder_inputs_targets(train_tagged_preprocessed_target, 
                                                                              target_tokenizer)

In [161]:
print(train_decoder_inputs[0], train_decoder_targets[0])

print(target_tokenizer.sequences_to_texts(train_decoder_inputs[:1]), 
      target_tokenizer.sequences_to_texts(train_decoder_targets[:1]))

[2, 604, 4] [604, 4, 3]
['<sos> geh .'] ['geh . <eos>']


In [162]:
max_encoding_len = len(max(train_encoder_inputs, key=len))
max_encoding_len

110

In [163]:
max_decoding_len = len(max(train_decoder_inputs, key=len))
max_decoding_len

90

In [164]:
padded_train_encoder_inputs = pad_sequences(train_encoder_inputs, max_encoding_len, padding='post', truncating='post')
padded_train_decoder_inputs = pad_sequences(train_decoder_inputs, max_decoding_len, padding='post', truncating='post')
padded_train_decoder_targets = pad_sequences(train_decoder_targets, max_decoding_len, padding='post', truncating='post')

In [165]:
print(padded_train_encoder_inputs[0])
print(padded_train_decoder_inputs[0])
print(padded_train_decoder_targets[0])

[49  2  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[  2 604   4   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0]
[604   4   3   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0  

In [166]:
target_tokenizer.sequences_to_texts([padded_train_decoder_inputs[0]])

['<sos> geh . <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk> <unk>']

In [167]:
embedding_dim = 128
hidden_dim = 256
default_dropout=0.2
batch_size = 32
epochs = 30

In [171]:
# The initial encoder input layer which will take in padded sequences. We're specifying
# a shape of None here but you can specify it upfront if you want since we
# know what the max encoding length is.
encoder_inputs = layers.Input(shape=[None], name='encoder_inputs')

# The embedding layer. Similar to what we did in the RNN demo.
encoder_embeddings = layers.Embedding(source_vocab_size, 
                                      embedding_dim,
                                      mask_zero=True,
                                      name='encoder_embeddings')

In [172]:
# Passing the input layer output to the embedding layer creates a link between the
# two. Input sequences will now flow into the embedding layer which will output
# a sequence of embeddings.
encoder_embedding_output = encoder_embeddings(encoder_inputs)


# We're not using any kind of attention mechanism in this model, so setting only
# return_state to True is enough. return_sequences remains False.
encoder_lstm = layers.LSTM(hidden_dim, 
                           return_state=True, 
                           dropout=default_dropout, 
                           name='encoder_lstm')

# Passing the embedding layer output to the LSTM layer creates another link.
# IMPORTANT: The LSTM always returns three values. When return_sequences is
# False, encoder_outputs and state_h are the SAME. When return_sequences is
# True, encoder_outputs contains the encoder hidden states from each time step.
#
# Side note: we won't be using encoder_outputs here so that variable can be 
# replaced with a _ if preferred.
encoder_outputs, state_h, state_c = encoder_lstm(encoder_embedding_output)

# The final hidden and cell/context states from the encoder will be the the
# initial states for the decoder.
encoder_states = (state_h, state_c)

In [173]:
decoder_inputs = layers.Input(shape=[None], name='decoder_inputs')


decoder_embeddings = layers.Embedding(target_vocab_size, 
                                      embedding_dim, 
                                      mask_zero=True,
                                      name='decoder_embeddings')


decoder_embedding_output = decoder_embeddings(decoder_inputs)

# Return sequences set to True.
decoder_lstm = layers.LSTM(hidden_dim,
                           return_sequences=True,
                           return_state=True,
                           dropout=default_dropout,
                           name='decoder_lstm')


# Set the decoder's initial state to the encoder's final output states. Since
# return_sequences is set to True, decoder_outputs is going to be a collection of
# the decoder's hidden state at each timestep. Also note that since we don't need
# the decoder's final hidden output and cell states, those are just set to _.
decoder_outputs, _, _ = decoder_lstm(decoder_embedding_output, initial_state=encoder_states)

# Have a softmax layer in the end to create a probability distribution for the output word.
decoder_dense = layers.Dense(target_vocab_size, activation='softmax', name='decoder_dense')

# The probability distribution for the output word.
y_proba = decoder_dense(decoder_outputs)

In [174]:
# Note how the model is taking two inputs in an array.
model = tf.keras.Model([encoder_inputs, decoder_inputs], y_proba, name='ger_en_seq2seq_nmt_no_attention')

model.compile(optimizer='adam', loss='sparse_categorical_crossentropy',  metrics='sparse_categorical_accuracy')
model.summary()

Model: "ger_en_seq2seq_nmt_no_attention"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 encoder_inputs (InputLayer  [(None, None)]               0         []                            
 )                                                                                                
                                                                                                  
 decoder_inputs (InputLayer  [(None, None)]               0         []                            
 )                                                                                                
                                                                                                  
 encoder_embeddings (Embedd  (None, None, 128)            2231424   ['encoder_inputs[0][0]']      
 ing)                                                               

In [175]:
# Saving this to a folder on my local machine.
filepath="Eng_gerNMTNoAttention/training1/cp.ckpt"

# Create a callback that saves the model's weights
cp_callback = tf.keras.callbacks.ModelCheckpoint(filepath=filepath,
                                                 save_weights_only=True,
                                                 verbose=1)

In [177]:
es_callback = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=3)

history = model.fit([padded_train_encoder_inputs, padded_train_decoder_inputs], padded_train_decoder_targets,
                     batch_size=batch_size,
                     epochs=epochs,
                     callbacks=[cp_callback, es_callback])

Epoch 1/30
 136/8172 [..............................] - ETA: 3:52:09 - loss: 6.5791 - sparse_categorical_accuracy: 0.1306

KeyboardInterrupt: 